In [1]:
import os
import math
import warnings
import botorch
import torch
import pickle
import gpytorch

import numpy as np
from torch import Tensor

from main_sim import *

from typing import Any, Callable, Dict, List, Optional, Tuple, Type, Union

from botorch.optim.optimize import optimize_acqf
from gpytorch.mlls import ExactMarginalLogLikelihood
from botorch.optim.fit import fit_gpytorch_torch
from botorch.utils.transforms import normalize, unnormalize
from botorch.test_functions.synthetic import SyntheticTestFunction
from botorch.test_functions.base import BaseTestProblem


from botorch.models import SingleTaskGP
from botorch.fit import fit_gpytorch_model
from gpytorch.mlls import ExactMarginalLogLikelihood

from botorch.acquisition.analytic import *
from botorch.acquisition.acquisition import AcquisitionFunction, OneShotAcquisitionFunction
from botorch.acquisition.knowledge_gradient import qKnowledgeGradient
from botorch.acquisition.utils import is_nonnegative

from botorch.optim.utils import columnwise_clamp
from botorch.optim.initializers import sample_points_around_best, initialize_q_batch_nonneg, initialize_q_batch

from botorch.utils.transforms import standardize, normalize, unnormalize
from botorch.utils.sampling import draw_sobol_samples

from botorch.logging import logger

from botorch.test_functions.synthetic import *
from test_functions_add import *

from HMC_pytorch.hmc import HMC, HMC_wc, unique
from scipy.stats.qmc import LatinHypercube

torch.random.manual_seed(1025)

<stdin>:1:10: fatal error: 'omp.h' file not found
#include <omp.h>
         ^~~~~~~
1 error generated.


[KeOps] Warning : omp.h header is not in the path, disabling OpenMP.
[KeOps] Warning : Cuda libraries were not detected on the system ; using cpu only mode


In [2]:
class Forrester(SyntheticTestFunction):
    r"""Forrester test function.

    1-dimensional function (evluated on `[0, 1]`):

        f(x) = (6x - 2)^2 x sin(12x - 4)

    f has two minimizers for its global minimum at 0.7572727 with f(x) = -6.02074
    """

    dim = 1
    _bounds = [(0, 1)]
    _optimal_value = -6.02074
    _optimizers = [(0.7572727)]

    def evaluate_true(self, X: Tensor) -> Tensor:
        return torch.pow(6 * X - 2, 2) * torch.sin(12 * X - 4)


class Gramacylee(SyntheticTestFunction):
    r"""Gramacylee test function.

    1-dimensional function (evaluated on `[0.5,2.5]`)

        f(x) = sin(10 * pi * x) / (2 * x) + (x - 1)^4

    f has multiple minimizers for its global minimum at 0.5484848 with f(x) = -0.8690084
    """

    dim = 1
    _bounds = [(0.5, 2.5)]
    _optimal_value = -0.8690084
    _optimizers = [(0.5484848)]

    def evaluate_true(self, X: Tensor) -> Tensor:
        return 0.5 * torch.sin(10 * math.pi * X) / X + torch.pow(X - 1, 4)


class Cos25(SyntheticTestFunction):
    r"""Cos25 test function.

    2-dimensional function (evaluated on `[-5 * math.pi, 5 * math.pi]`)

        f(x) = -cos(x[1]) - cos(x[2]) + 2

    f has 25 minimizers for its global minimum at (−4pi, −2pi, 0, 2pi, 4pi) x (−4pi, −2pi, 0, 2pi, 4pi)
    with f(x) = 0
    """

    dim = 2
    _bounds = [(-5 * math.pi, 5 * math.pi), (-5 * math.pi, 5 * math.pi)]
    _optimal_value = 0
    _optimizers = [(x, y) for x in [-4 * math.pi, -2 * math.pi, 0.0, 2 * math.pi, 4 * math.pi] for y in [-4 * math.pi, -2 * math.pi, 0.0, 2 * math.pi, 4 * math.pi]]

    def evaluate_true(self, X: Tensor) -> Tensor:
        return - torch.cos(X[:, 0]) - torch.sin(X[:, 1]) + 2

In [3]:
def initialize_func_data(n_init, test_fname, noise_err = None, negate = True):
    r""" Generate initial data X and Y                                                                                                                                                                      
                                                                                                                                                                                                            
    Args:                                                                                                                                                                                                   
        n_init: The number of initial observations                                                                                                                                                          
        test_func: The synthetic test function                                                                                                                                                              
    """

    if test_fname == "forrester":
        test_func = Forrester(noise_std = noise_err, negate = negate)
        X = torch.tensor([[1.000000], [0.998999], [0.997998], [0.996997], [0.995996], [0.994995],
                          [0.993994], [0.992993], [0.991992], [0.990991], [0.989990], [0.988989],
                          [0.987988], [0.986987], [0.985986], [0.984985], [0.983984], [0.982983],
                          [0.981982], [0.000001]])

    elif test_fname == "gramacylee":
        test_func = Gramacylee(noise_std = noise_err, negate = negate)
        X = torch.tensor([[2.500000], [2.479798], [2.459596], [2.439394], [2.419192], [2.398990],
                          [2.378788], [2.358586], [2.338384], [2.318182], [2.297980], [2.277778],
                          [2.257576], [2.237374], [2.217172], [2.196970], [2.176768], [2.156566],
                          [2.075758], [2.055556]])

    elif test_fname == "branin":
        test_func = Branin(noise_std = noise_err, negate = negate)
        X = torch.tensor([[-4.164435,  1.1083613], [ 6.528743, 14.0159310], [-4.698525,  3.2222688],
                          [ 7.539784, 12.6726376], [-3.259308,  0.9139629], [ 9.412842, 13.9978708],
                          [ 3.461396, 13.0616971], [ 9.995536, 13.8777384], [-3.106979,  2.5912381],
                          [ 4.747401, 10.0837920], [ 6.207700,  8.9837226], [ 7.221728,  9.3089992],
                          [ 4.267313,  9.9415172], [ 6.231150,  8.5540955], [-3.482933,  4.5695854],
                          [ 7.683778,  9.2480085], [-2.705795,  3.0076102], [ 7.992003,  9.3048741],
                          [ 7.421597,  7.8761192], [ 9.984521, 10.3204020]])

    elif test_fname == "bukin":
        test_func = Bukin(noise_std = noise_err, negate = negate)
        X = torch.tensor([[-14.782258, -2.31354514], [-11.733797, -2.73409899], [-12.577094, -1.73905221],
                          [ -5.551925, -2.95893695], [-14.752655, -0.83328976], [ -7.173028, -2.33736603],
                          [ -6.661439,  2.85186984], [-10.187024,  2.89301550], [ -5.942858,  2.02771586],
                          [-12.306895,  0.22623898], [-10.133092,  1.93559975], [-13.658440,  1.08699211],
                          [-12.114897,  2.08728042], [-13.417095, -0.97136246], [-11.839337, -1.85326349],
                          [ -8.973642, -1.92071465], [ -9.893225, -1.16856178], [ -8.735384, -0.81759850],
                          [ -7.044243,  2.19077014], [-12.719510, -0.81805064]])

    elif test_fname == "cos25":
        test_func = Cos25(noise_std = noise_err, negate = negate)
        X = torch.tensor([[  9.685261,  -9.453546], [-2.924930, -15.560466], [-9.287374, -15.484687],
                          [ -3.318463,   9.221838], [ 3.358412,   9.170040], [ 3.242191,   9.090878],
                          [ -9.638393,  15.379800], [ 9.363891,   9.027288], [-9.518078,   9.909692],
                          [ -9.358408,  -9.963629], [-9.294521,   2.590039], [ 3.676199,  -9.632932],
                          [  2.555179, -15.643330], [ 3.285424,  -2.558092], [10.025550,  -9.555165],
                          [-15.477495,  -8.854642], [ 3.448055,   3.684097], [ 8.852610,  15.435707],
                          [  9.438801,  -2.476219], [-9.449135,   3.826313]])
    elif test_fname == "sixhump":
        test_func = SixHumpCamel(noise_std = noise_err, negate = negate)
        X = torch.tensor([[-2.98328587, -1.572829267], [ 2.93459861,  1.626985202],
                          [ 2.93197648,  1.515288445], [ 2.76619446,    1.8223747],
                          [ 2.91231241, -1.984317077], [-0.46328674,  -1.99242722],
                          [ 0.13755351,   1.99900954], [-1.54981579, -1.996775675],
                          [ 0.55991782, -1.809796094], [-2.93046112,  -0.89865011],
                          [-2.90413808,   0.47318327], [ 0.87844217,   1.92421472],
                          [ 1.35101969,  -1.59447605], [ 2.91540293,   0.95101786],
                          [ 1.27818697,  -1.99910239], [ 2.94381701,   1.21146150],
                          [-2.93594566,  -0.25421254], [ 1.62054871,   1.99687208],
                          [ 1.31344912,   1.92525670], [ 0.78236839,   1.86286291]])

    elif test_fname == "ackley_6":
        test_func = Ackley(dim = 6, noise_std = noise_err, negate = negate)
        X = torch.tensor([[  -8.4315812, -17.3153522,  22.26262,  32.408878, -30.8963212,  -8.515600],
                          [  29.5453963,   1.6242493,  17.47136, -26.882310,  19.3924436,   8.618380],
                          [ -27.3038439, -28.1785901, -31.16398, -27.615676,  -8.5999745, -29.182121],
                          [ -25.5016057, -19.3620366, -22.09387,  32.053522,  29.8008629,  32.603029],
                          [  21.4021348, -21.2699596, -14.96034, -32.372521, -28.6480383, -27.973872],
                          [  20.4039755, -23.3293251, -22.49763,  24.721336,  12.2968080,  -9.095862],
                          [  21.7826166,   0.8571889, -30.78154, -22.708268,   1.5109326, -28.386300],
                          [  24.9551382,   2.9504992,  12.53158, -11.583200,  24.6215372, -29.422976],
                          [  16.4992870,   6.7816827, -28.54615, -29.139715, -17.0625433,  15.599798],
                          [ -17.1774412,  21.4889229, -19.78724,  24.435184, -17.2409164,   6.550005],
                          [ -31.4464921, -32.1108239,  27.96421,   3.806778, -28.9037047,  28.537022],
                          [ -26.1758454,  18.1160973,  26.23840,  -8.599178, -31.0760322, -16.431081],
                          [  -3.8424573,  21.5174936, -23.57530,   3.151505,  -8.3470128, -26.564979],
                          [ -27.3098929, -31.1795910, -28.84553,  -8.799973, -26.9299267,   7.576955],
                          [  13.7991309,  -9.6431461, -14.43782, -28.950492,  -0.3213235,  32.162446],
                          [  30.0414338,  21.9310283, -20.42654, -19.781156,  19.8889582,  31.633125],
                          [ -15.3538295, -14.0652300, -12.43462,  19.034870,  28.7355148,  28.836614],
                          [   3.8419054, -11.0712230, -28.43576, -32.166735,  -5.1937491, -13.465382],
                          [   0.3696409, -23.1028801,  20.13654,  22.470700, -12.3875389,  -2.613469],
                          [  31.6613292,  32.4172927, -16.05224,  16.105771,  -6.8701088,  -5.216815]])

    elif test_fname == "ackley_10":
        test_func = Ackley(dim = 10, noise_std = noise_err, negate = negate)
        X = torch.tensor([[ 32.3877971,  26.501815,  22.299357, -26.040931, -30.281209,  21.511766, -30.6450437,   3.3848704,  -3.747893,   8.421723],
                          [ -0.4018215,  28.605290, -32.462399, -31.150627,   2.292289, -30.278813, -10.5155881, -29.1811123,  -8.628492,  22.863357],
                          [  8.3869819,  19.429193, -13.957686,  -5.509045, -31.332671, -32.226475,  -2.1937338,  25.5622947,  16.517047, -23.703583],
                          [-28.0666682,  21.768969,  26.401945, -22.478409,   3.790090,  -6.285940, -14.2455309, -31.1224398,  32.593790,  19.583546],
                          [ 28.1266138, -30.221196,   5.582365,  28.450221,   8.392860,   4.626442,  21.8653813,  17.3430815,  18.442893, -21.848996],
                          [-23.8984996,  22.107031,  23.799612,  -9.613451,  -2.312701,  32.471670,   7.4874878,  12.7587307,  -5.315025,  31.492374],
                          [  4.4944473, -22.318968, -30.107162,  -2.360623,  23.108870, -32.179005, -29.8295934,   3.5907822,  -2.515658,   9.514477],
                          [  3.2535941,  29.247259,  -4.555638, -15.568783, -17.402359,  32.761535, -26.9948812,  23.5434795,   5.071997,  -3.649046],
                          [-26.4332415, -11.818434,  13.259183, -16.497368,  24.822449,  28.089611,  10.5784070, -23.0773747, -24.634559,   2.415521],
                          [ 12.0220716, -23.303859,  22.247031, -32.295907,  21.254176,  -8.062512, -31.7556683,  23.6022372, -28.132989, -29.306295],
                          [ 28.4457317, -31.900993,  11.725527,  13.701073,  16.253916,  17.180442,  23.5799218, -16.0500937, -14.822065, -26.369948],
                          [ 22.6049354,   3.144253,  -3.647890,  15.606272,  22.827076,  15.700359,   0.2790672, -26.2114408,  32.471867,  -8.332550],
                          [  2.8112157, -30.208566, -28.262294,  23.307709,   6.985436, -21.499411,  30.4090958, -14.0798504, -29.016723,  -6.497402],
                          [-29.0509108, -31.388581,  -1.786883,  19.682283,  21.778707,  25.730137,   5.7497075,  -0.7247546, -22.874676,  17.616220],
                          [-30.7877591,   6.088867,  -8.743845,  28.313675, -15.652337, -30.404829, -13.9825939, -19.1323187, -17.318556,  23.295580],
                          [-28.9772533, -12.650350, -30.481810, -24.112105, -21.858462,  12.936587, -19.3420499,  14.1864457, -11.306360, -28.364213],
                          [ -2.7898445, -27.741687, -18.224266,  -1.718605, -12.544992,  29.952344, -17.9233362,  21.5872144, -14.626348,  28.231862],
                          [ 32.2619098, -32.080755,  32.409694,  -4.724463, -27.900768, -10.824707,  -1.0797286,  -6.3286346,  -7.783757, -19.469783],
                          [ 12.0866209,  -1.431096,  23.915167, -31.290300, -24.881174,  12.410466,  24.9632130,  23.9311524,  29.463442,   7.787244],
                          [ 30.0908081,   8.790618,  -5.752885,   7.907234, -28.152526,  26.106973,  28.5196678, -32.7164891,  11.628945,  23.099142]])
    
    elif test_fname == "hartmann":
        test_func = Hartmann(noise_std = noise_err, negate = negate)
        X = torch.tensor([[0.917491171, 0.31974692224, 0.8519555288, 0.2657330546, 0.957700116, 0.482562402],
                          [0.770659772, 0.11653138814, 0.9827676432, 0.7120511250, 0.862200331, 0.824269375],
                          [0.957141051, 0.96626577619, 0.0014717572, 0.8152684912, 0.426642967, 0.375274350],
                          [0.886041189, 0.14163601818, 0.6169752553, 0.3130856985, 0.882597998, 0.889040401],
                          [0.995713057, 0.19697296061, 0.3936798437, 0.8782727711, 0.525233528, 0.422771374],
                          [0.117185918, 0.14694812358, 0.2073540508, 0.9181328288, 0.854374080, 0.832469278],
                          [0.855443630, 0.73070535786, 0.0233771447, 0.7360681910, 0.014971097, 0.615451148],
                          [0.879061422, 0.09180245525, 0.8522684642, 0.3053059964, 0.761649901, 0.404634016],
                          [0.236442405, 0.53545816569, 0.3102159053, 0.9875037423, 0.357519740, 0.995389137],
                          [0.864053558, 0.13308687159, 0.3983544284, 0.4906786461, 0.775472443, 0.509765224],
                          [0.554277961, 0.10227611987, 0.1862053028, 0.7850359816, 0.191730443, 0.015518636],
                          [0.442280527, 0.65666235588, 0.7902077872, 0.1150079516, 0.849898158, 0.992224550],
                          [0.657576123, 0.25019891234, 0.7694613419, 0.7709350730, 0.514761515, 0.274110735],
                          [0.235498313, 0.03543934086, 0.5375724582, 0.7697524345, 0.903988519, 0.965331213],
                          [0.793743405, 0.98793104268, 0.1767423782, 0.7050258562, 0.688176861, 0.370083976],
                          [0.823678245, 0.66690863087, 0.8832108213, 0.2357671564, 0.012945082, 0.409940149],
                          [0.337776616, 0.18705414305, 0.3137723736, 0.7475840838, 0.029630197, 0.114214398],
                          [0.023633718, 0.21494590305, 0.3058558111, 0.6690362883, 0.864621475, 0.495771657],
                          [0.861791465, 0.05977980117, 0.1290991304, 0.4225857565, 0.633873692, 0.421955053],
                          [0.582552165, 0.45579134882, 0.6629171574, 0.1349195810, 0.773142474, 0.300817263]])

    elif test_fname == "michalewicz_2":
        test_func = Michalewicz(dim = 2, noise_std = noise_err, negate = negate)
        X = torch.tensor([[0.087826736,  0.069116402], [0.012817273,  0.163849103], [0.063912353,  0.127418801], [0.186616258,  0.035294068],
                          [0.013336331,  0.238665764], [ 3.11981132, 0.2261725713], [3.078576702,  0.281922065], [3.112934513,  2.267103644],
                          [3.046981897,  3.101754896], [ 0.52718394, 0.2348220495], [ 0.60564961, 0.4299477234], [0.380039916,  0.061250420],
                          [0.286234941,  0.391561785], [0.844867621,  2.377461780], [1.150224611,  2.985051407], [1.404788955,  3.124873028],
                          [1.188944177,  1.982791676], [1.419435594,  0.189363624], [2.781520844,  2.430745204], [1.465455198,  2.320642085]])

    elif test_fname == "michalewicz_5":
        test_func = Michalewicz(dim = 5, noise_std = noise_err, negate = negate)
        X = torch.tensor([[0.787318919, 0.491606242, 0.298278284, 2.1974807450, 2.4119346578],
                          [0.721429263, 2.212243160, 2.637477647, 0.0683040679, 0.4677493912],
                          [2.862951550, 2.365068917, 0.091228582, 1.5165600902, 1.3381990304],
                          [1.045920222, 3.073538290, 0.478391403, 2.1202814527, 3.1136793845],
                          [0.935013315, 0.157242448, 0.833762636, 0.1005464444, 3.1379405532],
                          [1.205626397, 1.993811891, 1.982791119, 2.8160636157, 0.1530387971],
                          [0.496999140, 0.871131496, 1.751056055, 0.0873600512, 0.6793332145],
                          [2.755095777, 2.106297757, 0.296810129, 3.0399481077, 0.3236964075],
                          [2.556405316, 1.958477190, 0.557985346, 1.5578931962, 3.0608311953],
                          [2.752306461, 2.570281799, 0.262265440, 0.4440758386, 0.2006607933],
                          [0.715304046, 1.819724148, 1.552842628, 3.0466659226, 0.2023830948],
                          [2.975096518, 0.589005422, 0.540205807, 2.7265113883, 1.1301830361],
                          [0.628304953, 1.789597707, 1.731257797, 0.5290244296, 0.3354537324],
                          [0.787717892, 1.101795318, 1.834661012, 1.3508852570, 1.6384384382],
                          [0.039648077, 0.211846406, 0.295728774, 3.1346705224, 0.8647835768],
                          [0.675738180, 1.393184304, 2.434587546, 3.1034714201, 2.5551569622],
                          [1.560820565, 1.051741177, 1.423213938, 1.4488404566, 2.5762628236],
                          [0.409111599, 0.735620955, 0.362685025, 0.1765729416, 2.6117614115],
                          [0.194047216, 0.263685426, 1.575667007, 3.0043694090, 2.1862486838],
                          [2.348568122, 0.264687116, 2.565045098, 1.6332440330, 0.1695581587]])
    elif test_fname == "michalewicz_10":
        test_func = Michalewicz(dim = 10, noise_std = noise_err, negate = negate)
        X = torch.tensor([[2.617447727, 3.065329431, 2.422405869, 3.036980923, 1.402111305, 1.118501971, 0.590740389, 1.945707385, 0.96484845, 3.131331040],
                          [1.238596320, 2.130405745, 0.072068114, 1.738235515, 1.601412122, 2.918258999, 0.020515675, 3.124203006, 0.44892957, 2.015495388],
                          [2.634452221, 1.020393286, 2.105202820, 2.757223125, 0.389833004, 0.027629861, 0.584826389, 0.297620412, 3.04685696, 1.680012507],
                          [0.286469860, 2.418207800, 0.867314255, 2.890473724, 3.062866275, 1.426638774, 0.410860987, 3.038424612, 0.29145008, 0.503104666],
                          [0.041531069, 3.136724023, 0.534231370, 2.038309846, 3.136906566, 0.331969503, 2.806080290, 0.076829859, 2.94112890, 2.748253870],
                          [1.438272709, 1.179511654, 1.583867126, 1.620336247, 1.395131895, 2.092237328, 1.930954834, 3.032892612, 3.12704704, 0.591447568],
                          [1.791828823, 2.138841320, 3.012097407, 0.612641434, 1.109302539, 1.810821762, 1.131879570, 0.404351924, 1.37570001, 0.790546113],
                          [1.580005179, 0.479237862, 0.613474092, 0.046072891, 1.083562504, 1.482787103, 1.948714906, 0.555948022, 1.40153638, 0.895133979],
                          [2.894986154, 2.996735589, 2.463563421, 2.818037508, 2.004778521, 1.033847395, 1.511920760, 2.852389332, 1.01691432, 0.557900942],
                          [2.982851764, 1.880133667, 0.597607647, 2.518890307, 2.984647306, 0.326556418, 1.625635481, 1.580805077, 1.15784618, 1.924894032],
                          [1.387413831, 1.864921908, 1.019784121, 0.393237772, 2.864333259, 1.998834075, 1.112369671, 0.198879757, 1.83747667, 1.134125607],
                          [0.731710602, 2.001500634, 0.183262094, 2.217542992, 1.082039463, 1.744603837, 0.085006682, 2.043698072, 2.09844468, 0.598041687],
                          [1.253923632, 0.062007563, 1.577969221, 1.171732615, 0.796679718, 2.951514330, 1.255112423, 2.300968096, 1.41627476, 1.801682808],
                          [3.003156565, 0.185237569, 2.978221573, 1.796788637, 0.924301433, 1.040094736, 2.883730702, 2.151621161, 2.84872636, 0.829716540],
                          [0.721398745, 0.701933431, 2.571683647, 3.033219674, 1.240861292, 0.918585093, 2.300837562, 0.084058532, 3.02468093, 0.901128378],
                          [0.602291607, 0.272366672, 3.112129095, 2.251176550, 2.220469758, 2.503018530, 2.158829028, 2.906593698, 2.07943676, 2.152249278],
                          [0.508659922, 0.897082500, 0.534336638, 0.463481491, 0.415914667, 0.547196687, 2.993234168, 1.920102885, 0.74423709, 0.618257110],
                          [3.040408146, 2.422149474, 2.042527148, 2.119102513, 0.926953234, 2.544156645, 1.705974817, 2.173732966, 0.59878622, 2.729003869],
                          [3.124342488, 1.840771003, 1.783976727, 1.587334205, 1.307435032, 1.175014395, 0.230506585, 1.057695037, 1.28254244, 2.795696359],
                          [2.504012032, 2.232894954, 2.741109540, 1.686181937, 0.078694426, 0.781589316, 1.851317116, 3.120428890, 0.82601631, 0.436859660]])

    X_init = X[:n_init, :]
    y_init = test_func(X_init)
    return test_func, X_init, y_init

In [4]:
def optim_benchmark(dfn, acq, output_dir, n_sugs = 1):
    if dfn in ("forrester", "gramacylee", "branin", "bukin", "cos25", "sixhump", "michalewicz_2"):
        n_init = 3
        if dfn == "forrester":
            threshold_value = -0.5
            budget = 30
        elif dfn == "gramacylee":
            threshold_value = 0.
            budget = 50
        elif dfn == "branin":
            threshold_value = 1.
            budget = 80
        elif dfn == "bukin":
            threshold_value = 10.
            budget = 150
        elif dfn == "cos25":
            threshold_value = 0.1
            budget = 250
        elif dfn == "sixhump":
            threshold_value = -0.5
            budget = 150
        elif dfn == "michalewicz_2":
            threshold_value = -1.5
            budget = 150
    elif dfn in ("ackley_6", "hartmann"):
        n_init = 7
        if dfn == "ackley_6":
            threshold_value = 5.
            budget = 250
        elif dfn == "hartmann":
            threshold_value = -2.8
            budget = 250
    elif dfn in ("ackley_10", "michalewicz_10"):
        n_init = 11
        if dfn == "ackley_10":
            threshold_value = 5.
            budget = 250
        elif dfn == "michalewicz_10":
            threshold_value = -5.5
            budget = 250
    else:
        n_init = 6
        threshold_value = -3.5
        budget = 250
        
    M = 30
    res_acq = []
    seed = 1025
    for j in range(M):
        obj, X, Y = initialize_func_data(n_init, dfn, noise_err = None, negate = True)
        Y = Y.view(-1, 1)
        print(f"Iteration {j}")
        for i in range(budget):
            train_X = normalize(X, obj.bounds)
            model = botorch.models.SingleTaskGP(train_X, Y)
            mll = ExactMarginalLogLikelihood(model.likelihood, model)
            try:
                fit_gpytorch_torch(mll, options={"maxiter": 3000, "lr": 0.01, "disp": False})
            except:
                try:
                    with gpytorch.settings.cholesky_jitter(1e-1):
                        fit_gpytorch_torch(mll, options={"maxiter": 3000, "lr": 0.01, "disp": False})
                except:
                    break
                    
            if acq == "ei":
                acquisition = botorch.acquisition.analytic.ExpectedImprovement(model, torch.max(Y), maximize=True)
                candidates, acqui_value = optimize_acqf(acq_function=acquisition, 
                                                bounds = torch.tensor([[0.] * obj.dim, [1.] * obj.dim]),
                                                # bounds=test_fun.bounds,
                                                q=1,
                                                num_restarts=20,
                                                raw_samples=512,
                                                sequential=False,
                                                )
            elif acq == "ei_t":
                acquisition = ExpectedImprovement(model = model, best_f = threshold_value, maximize = True)
                candidates, acqui_value = optimize_acqf(acq_function=acquisition, 
                                                bounds = torch.tensor([[0.] * obj.dim, [1.] * obj.dim]),
                                                # bounds=test_fun.bounds,
                                                q=1,
                                                num_restarts=20,
                                                raw_samples=512,
                                                sequential=False,
                                                )
            elif acq == "adj_ei":
                acquisition = AdjustedDistExpectedImprovement(model = model, best_f = Y.max(), X_keep = train_X, maximize = True)
                candidates, acqui_value = optimize_acqf(acq_function=acquisition, 
                                                bounds = torch.tensor([[0.] * obj.dim, [1.] * obj.dim]),
                                                # bounds=test_fun.bounds,
                                                q=1,
                                                num_restarts=20,
                                                raw_samples=512,
                                                sequential=False,
                                                )
            elif acq == "adj_ei_t":
                acquisition = AdjustedDistExpectedImprovement(model = model, best_f = threshold_value, X_keep = train_X, maximize = True)
                candidates, acqui_value = optimize_acqf(acq_function=acquisition, 
                                                bounds = torch.tensor([[0.] * obj.dim, [1.] * obj.dim]),
                                                # bounds=test_fun.bounds,
                                                q=1,
                                                num_restarts=20,
                                                raw_samples=512,
                                                sequential=False,
                                                )
            elif acq == "poi":
                acquisition = ProbabilityOfImprovement(model = model, best_f = Y.max(), maximize = True)
                candidates, acqui_value = optimize_acqf(acq_function=acquisition, 
                                                bounds = torch.tensor([[0.] * obj.dim, [1.] * obj.dim]),
                                                # bounds=test_fun.bounds,
                                                q=1,
                                                num_restarts=20,
                                                raw_samples=512,
                                                sequential=False,
                                                )
            elif acq == "poi_t":
                acquisition = ProbabilityOfImprovement(model = model, best_f = threshold_value, maximize = True)
                candidates, acqui_value = optimize_acqf(acq_function=acquisition, 
                                                bounds = torch.tensor([[0.] * obj.dim, [1.] * obj.dim]),
                                                # bounds=test_fun.bounds,
                                                q=1,
                                                num_restarts=20,
                                                raw_samples=512,
                                                sequential=False,
                                                )
            elif acq == "adj_poi":
                acquisition = AdjustedDistProbabilityOfImprovement(model = model, best_f = Y.max(), X_keep = train_X, maximize = True)
                candidates, acqui_value = optimize_acqf(acq_function=acquisition, 
                                                bounds = torch.tensor([[0.] * obj.dim, [1.] * obj.dim]),
                                                # bounds=test_fun.bounds,
                                                q=1,
                                                num_restarts=20,
                                                raw_samples=512,
                                                sequential=False,
                                                )
            elif acq == "adj_poi_t":
                acquisition = AdjustedDistProbabilityOfImprovement(model = model, best_f = threshold_value, X_keep = train_X, maximize = True)
                candidates, acqui_value = optimize_acqf(acq_function=acquisition, 
                                                bounds = torch.tensor([[0.] * obj.dim, [1.] * obj.dim]),
                                                # bounds=test_fun.bounds,
                                                q=1,
                                                num_restarts=20,
                                                raw_samples=512,
                                                sequential=False,
                                                )
            elif acq == "ucb":
                beta = choose_beta(obj.dim, i + 1)
                acquisition = UpperConfidenceBound(model = model, beta = beta, maximize = True)
                candidates, acqui_value = optimize_acqf(acq_function=acquisition, 
                                                bounds = torch.tensor([[0.] * obj.dim, [1.] * obj.dim]),
                                                # bounds=test_fun.bounds,
                                                q=1,
                                                num_restarts=20,
                                                raw_samples=512,
                                                sequential=False,
                                                )
            elif acq == "adj_ucb":
                beta = choose_beta(obj.dim, i + 1)
                acquisition = AdjustedDistUpperConfidenceBound(model = model, beta = beta, X_keep = train_X, maximize = True)
                candidates, acqui_value = optimize_acqf(acq_function=acquisition, 
                                                bounds = torch.tensor([[0.] * obj.dim, [1.] * obj.dim]),
                                                # bounds=test_fun.bounds,
                                                q=1,
                                                num_restarts=20,
                                                raw_samples=512,
                                                sequential=False,
                                                )
            elif acq == "pr":
                acquisition = ProbabilityRatio(model = model, best_f = Y.max(), maximize = True)
                candidates, acqui_value = optimize_acqf(acq_function=acquisition, 
                                                bounds = torch.tensor([[0.] * obj.dim, [1.] * obj.dim]),
                                                # bounds=test_fun.bounds,
                                                q=1,
                                                num_restarts=20,
                                                raw_samples=512,
                                                sequential=False,
                                                )
            elif acq == "pr_t":
                acquisition = ProbabilityRatio(model = model, best_f = threshold_value, maximize = True)
                candidates, acqui_value = optimize_acqf(acq_function=acquisition, 
                                                bounds = torch.tensor([[0.] * obj.dim, [1.] * obj.dim]),
                                                # bounds=test_fun.bounds,
                                                q=1,
                                                num_restarts=20,
                                                raw_samples=512,
                                                sequential=False,
                                                )
            elif acq == "adj_pr":
                acquisition = AdjustedDistProbabilityRatio(model = model, best_f = Y.max(), X_keep = train_X, maximize = True)
                candidates, acqui_value = optimize_acqf(acq_function=acquisition, 
                                                bounds = torch.tensor([[0.] * obj.dim, [1.] * obj.dim]),
                                                # bounds=test_fun.bounds,
                                                q=1,
                                                num_restarts=20,
                                                raw_samples=512,
                                                sequential=False,
                                                )
            elif acq == "adj_pr_t":
                acquisition = AdjustedDistProbabilityRatio(model = model, best_f = threshold_value, X_keep = train_X, maximize = True)
                candidates, acqui_value = optimize_acqf(acq_function=acquisition, 
                                                bounds = torch.tensor([[0.] * obj.dim, [1.] * obj.dim]),
                                                # bounds=test_fun.bounds,
                                                q=1,
                                                num_restarts=20,
                                                raw_samples=512,
                                                sequential=False,
                                                )
            elif acq == "ts":
                ts_sampler = "cholesky"
                n_candidates = min(5000, max(2000, 200 * X.shape[-1]))
                use_keops = False
                assert ts_sampler in ("cholesky", "ciq", "rff", "lanczos")
                kernel_kwargs = {"nu": 2.5, "ard_num_dims": X.shape[-1]}
                if ts_sampler == "rff":
                    base_kernel = RFFKernel(**kernel_kwargs, num_samples = 1024)
                else:
                    base_kernel = (
                        KmaternKernel(**kernel_kwargs) if use_keops else MaternKernel(**kernel_kwargs)
                    )
                covar_module = ScaleKernel(base_kernel)

                X_double = train_X.to(dtype = torch.double)
                Y_double = Y.to(dtype = torch.double)
                mdl_double = SingleTaskGP(X_double, Y_double)
                mll_double = ExactMarginalLogLikelihood(mdl_double.likelihood, mdl_double)
                _ = fit_gpytorch_model(mll_double)

                sobol = SobolEngine(X.shape[-1], scramble = True)
                X_cand = sobol.draw(n_candidates)
                X_cand = X_cand.to(dtype = torch.double, device = device)

                with ExitStack() as es:
                    if ts_sampler == "cholesky":
                        es.enter_context(gpts.max_cholesky_size(float("Inf")))
                    elif ts_sampler == "ciq":
                        es.enter_context(gpts.fast_computations(covar_root_decomposition = True))
                        es.enter_context(gpts.max_cholesky_size(0))
                        es.enter_context(gpts.ciq_samples(True))
                        es.enter_context(gpts.minres_tolerance(2e-3))
                        es.enter_context(gpts.num_contour_quadrature(15))
                    elif ts_sampler =="lanczos":
                        es.enter_context(gpts.fast_computations(covar_root_decomposition = True))
                        es.enter_context(gpts.max_cholesky_size(0))
                        es.enter_context(gpts.ciq_samples(False))
                    elif ts_sampler == "rff":
                        es.enter_context(gpts.fast_computations(covar_root_decomposition = True))

                    thompson_sampling = MaxPosteriorSampling(model = mdl_double, replacement = False)
                    candidates = thompson_sampling(X_cand, num_samples = batch_size)
            elif acq == "mes":
                candidate_set = torch.rand(1000, obj.dim, device = device, dtype = torch.double)
                # candidate_set = obj.bounds[0] + (obj.bounds[1] - obj.bounds[0]) * candidate_set
                X_double = train_X.to(dtype = torch.double)
                Y_double = Y.to(dtype = torch.double)
                mdl_double = SingleTaskGP(X_double, Y_double)
                mll_double = ExactMarginalLogLikelihood(mdl_double.likelihood, mdl_double)
                fit_gpytorch_model(mll_double)
                acquisition = qMaxValueEntropy(mdl_double, candidate_set)
                candidates, acqui_value = optimize_acqf(acq_function=acquisition, 
                                                bounds = torch.tensor([[0.] * obj.dim, [1.] * obj.dim]),
                                                # bounds=test_fun.bounds,
                                                q=1,
                                                num_restarts=20,
                                                raw_samples=512,
                                                sequential=False,
                                                )
            elif acq == "tr_ts":
                n_candidates = min(5000, max(2000, 200 * train_X.shape[-1]))
                state = TurboState(obj.dim, batch_size=batch_size)
                X_double = train_X.to(dtype = torch.double)
                Y_double = Y.to(dtype = torch.double)
                likelihood_double = GaussianLikelihood(noise_constraint=Interval(1e-8, 1e-3))
                covar_module = ScaleKernel(  # Use the same lengthscale prior as in the TuRBO paper
                    MaternKernel(nu=2.5, ard_num_dims=obj.dim, lengthscale_constraint=Interval(0.005, 4.0))
                )
                model_double = SingleTaskGP(X_double, Y_double, covar_module=covar_module, likelihood=likelihood_double)
                # model_double = SingleTaskGP(X_double, Y_double)
                mll = ExactMarginalLogLikelihood(model_double.likelihood, model_double)
                _ = fit_gpytorch_model(mll)

                # scale the TR to be proportional to the lengthscales
                x_center = X_double[Y_double.argmax(), :].clone()
                weights = model_double.covar_module.base_kernel.lengthscale.squeeze().detach()
                if obj.dim > 1:
                    weights = weights / weights.mean()
                    weights = weights / torch.prod(weights.pow(1.0 / len(weights)))
                else:
                    weights = torch.tensor(1.0)
                tr_lb = torch.clamp(x_center - weights * state.length / 2.0, 0.0, 1.0)
                tr_ub = torch.clamp(x_center + weights * state.length / 2.0, 0.0, 1.0)
                sobol = SobolEngine(obj.dim, scramble = True)
                pert = sobol.draw(n_candidates).to(dtype = torch.double, device = device)
                pert = tr_lb + (tr_ub - tr_lb) * pert

                # create a perturbation mask
                prob_perturb = min(20.0 / obj.dim, 1.0)
                mask = (
                    torch.rand(n_candidates, obj.dim, dtype = torch.double, device = device)
                    <= prob_perturb
                )
                ind = torch.where(mask.sum(dim = 1) == 0)[0]
                if len(ind) > 0:
                    mask[ind, torch.randint(0, obj.dim - 1, size = (len(ind), ), device = device)] = 1
                else:
                    mask = mask

                # create candidate points from the perturbations and the mask
                X_cand = x_center.expand(n_candidates, obj.dim).clone()
                X_cand[mask] = pert[mask]

                # sample on the candidate points
                thompson_sampling = MaxPosteriorSampling(model = model_double, replacement = False)
                with torch.no_grad():
                    with manual_seed(seed):
                        candidates = thompson_sampling(X_cand, num_samples = batch_size)
            elif acq == "tr_ei":
                n_candidates = min(5000, max(2000, 200 * train_X.shape[-1]))
                state = TurboState(obj.dim, batch_size=batch_size)
                X_double = train_X.to(dtype = torch.double)
                Y_double = Y.to(dtype = torch.double)
                likelihood_double = GaussianLikelihood(noise_constraint=Interval(1e-8, 1e-3))
                covar_module = ScaleKernel(  # Use the same lengthscale prior as in the TuRBO paper
                    MaternKernel(nu=2.5, ard_num_dims=obj.dim, lengthscale_constraint=Interval(0.005, 4.0))
                )
                model_double = SingleTaskGP(X_double, Y_double, covar_module=covar_module, likelihood=likelihood_double)
                # model_double = SingleTaskGP(X_double, Y_double)
                mll = ExactMarginalLogLikelihood(model_double.likelihood, model_double)
                _ = fit_gpytorch_model(mll)

                # scale the TR to be proportional to the lengthscales
                x_center = X_double[Y_double.argmax(), :].clone()
                weights = model_double.covar_module.base_kernel.lengthscale.squeeze().detach()
                if obj.dim > 1:
                    weights = weights / weights.mean()
                    weights = weights / torch.prod(weights.pow(1.0 / len(weights)))
                else:
                    weights = torch.tensor(1.0)
                tr_lb = torch.clamp(x_center - weights * state.length / 2.0, 0.0, 1.0)
                tr_ub = torch.clamp(x_center + weights * state.length / 2.0, 0.0, 1.0)
                EI = qExpectedImprovement(model_double, Y_double.max(), maximize = True)
                with manual_seed(seed):
                    candidates, acq_value = optimize_acqf(
                        EI,
                        bounds = torch.stack([tr_lb, tr_ub]),
                        q = batch_size,
                        num_restarts = 20,
                        raw_samples = 512,
                    )

            ori_X_next = unnormalize(candidates, obj.bounds)
            Y_next = obj(ori_X_next).view(-1, 1)
            X = torch.cat((X, ori_X_next), dim=0)
            Y = torch.cat((Y, Y_next), dim=0)
            for k in range(n_sugs):
                print(f"Iteration: {i + k + 1}: X = {ori_X_next[k].numpy()} | y = {-Y_next[k].numpy()}")
        # save to numpy
        resX_np = X.cpu().detach().numpy()
        resY_np = Y.cpu().detach().numpy()
        res_np = np.hstack([resX_np, -resY_np])
        # append to the result list
        res_acq.append(res_np)
        
    # save to a file
    outputfile = os.path.join(output_dir,"optim_" + dfn + "_" + acq + "_rep_30.pickle")
    with open(outputfile, 'wb') as f:
        pickle.dump(res_acq, f)

In [5]:
dfn_list = ["bukin", "sixhump", "michalewicz_2", "hartmann", "ackley_6", 
            "ackley_10", "michalewicz_5", "michalewicz_10"]
# 
acq_list = ["ei", "poi", "ucb", "ts", "mes", "pr", "ei_t", "adj_ei", "adj_ei_t", "poi_t", "adj_poi", "adj_poi_t", "adj_ucb", 
            "pr_t", "adj_pr", "adj_pr_t", "tr_ts", "tr_ei"]

output_dir = "/Users/liao/Documents/BObystep/python_botorch/results/"
batch_size = 1
n_sugs = 1

In [6]:
dfn_list[:4]

['bukin', 'sixhump', 'michalewicz_2', 'hartmann']

In [ ]:
for acq in acq_list[1:]:
    for dfn in dfn_list[:4]:
        print(acq)
        print(dfn)
        optim_benchmark(dfn, acq, output_dir)

poi
bukin
Iteration 0
Iteration: 1: X = [-10.793798     0.39136457] | y = [87.96795]
Iteration: 2: X = [-5.4749327  1.657207 ] | y = [116.55526]
Iteration: 3: X = [-5.  3.] | y = [165.88124]
Iteration: 4: X = [-9.016155   1.0530682] | y = [49.01572]
Iteration: 5: X = [-8.989121  2.59592 ] | y = [133.72162]
Iteration: 6: X = [-12.443461   -1.5609865] | y = [176.35889]
Iteration: 7: X = [-6.1395416  2.723198 ] | y = [153.21361]
Iteration: 8: X = [-13.189455  -2.085701] | y = [195.6161]
Iteration: 9: X = [-11.470509   -1.1438851] | y = [156.84618]
Iteration: 10: X = [-9.814638  2.559681] | y = [126.35096]
Iteration: 11: X = [-8.754577   -0.36486673] | y = [106.374695]
Iteration: 12: X = [-11.496841    2.8135939] | y = [122.15507]
Iteration: 13: X = [-14.843161    0.8594165] | y = [115.96986]
Iteration: 14: X = [-13.789257    2.2826939] | y = [61.783962]
Iteration: 15: X = [-8.031369 -2.551921] | y = [178.81985]
Iteration: 16: X = [-7.2848563  -0.15952826] | y = [83.106606]
Iteration: 17: 

Iteration: 133: X = [-8.343836    0.07077074] | y = [79.100395]
Iteration: 134: X = [-7.6783304 -0.8362193] | y = [119.429535]
Iteration: 135: X = [-12.686935   2.556489] | y = [97.33595]
Iteration: 136: X = [-14.113267    -0.61147046] | y = [161.389]
Iteration: 137: X = [-6.1922884  2.4414072] | y = [143.4941]
Iteration: 138: X = [-6.794323    0.68355274] | y = [47.14092]
Iteration: 139: X = [-12.226326    -0.40019512] | y = [137.68219]
Iteration: 140: X = [-12.307927    2.2064352] | y = [83.18464]
Iteration: 141: X = [-11.246937   -2.1343007] | y = [184.38264]
Iteration: 142: X = [-8.076542    0.27799463] | y = [61.200165]
Iteration: 143: X = [-5.560457    0.34469128] | y = [18.887014]
Iteration: 144: X = [-6.741638  -2.3837109] | y = [168.5024]
Iteration: 145: X = [-7.8885503   0.90362763] | y = [53.062172]
Iteration: 146: X = [-6.547559  -2.1498914] | y = [160.61462]
Iteration: 147: X = [-9.250331    0.40922594] | y = [66.82518]
Iteration: 148: X = [-12.466011     0.54910684] | y =

Iteration: 115: X = [-6.3262167 -2.1436396] | y = [159.53125]
Iteration: 116: X = [-6.515497 -2.775837] | y = [178.93018]
Iteration: 117: X = [-6.894251  -2.9450526] | y = [184.97319]
Iteration: 118: X = [-11.398211  -2.734898] | y = [200.86441]
Iteration: 119: X = [-13.676827     0.50795984] | y = [116.76706]
Iteration: 120: X = [-14.66213     0.7630191] | y = [117.80747]
Iteration: 121: X = [-12.5864315  -0.9334514] | y = [158.6964]
Iteration: 122: X = [-9.884987  -1.9591973] | y = [171.35829]
Iteration: 123: X = [-13.07632     1.4984736] | y = [46.012028]
Iteration: 124: X = [-12.195359   -1.4734223] | y = [172.08852]
Iteration: 125: X = [-13.222553     0.87441516] | y = [93.5172]
Iteration: 126: X = [-6.762764   1.4845495] | y = [101.38324]
Iteration: 127: X = [-14.502772  -1.063885] | y = [178.011]
Iteration: 128: X = [-12.431996  -2.451428] | y = [199.94864]
Iteration: 129: X = [-7.4326305  -0.91361356] | y = [121.10637]
Iteration: 130: X = [-10.433743    1.2537012] | y = [40.633

Iteration: 97: X = [-14.586719    0.3291099] | y = [134.15826]
Iteration: 98: X = [-7.7591662 -1.3120909] | y = [138.37477]
Iteration: 99: X = [-11.155878    -0.31312656] | y = [124.81792]
Iteration: 100: X = [-13.822655    1.6488914] | y = [51.20133]
Iteration: 101: X = [-11.243307    1.0478888] | y = [46.51305]
Iteration: 102: X = [-11.603225    2.2721243] | y = [96.233284]
Iteration: 103: X = [-5.021779    0.06879997] | y = [42.872986]
Iteration: 104: X = [-13.695019   2.516531] | y = [80.09915]
Iteration: 105: X = [-12.900036    -0.75106764] | y = [155.43741]
Iteration: 106: X = [-6.9236317  2.584742 ] | y = [145.12988]
Iteration: 107: X = [-11.942867    0.8053758] | y = [78.819496]
Iteration: 108: X = [-11.577621   -1.6149435] | y = [171.92728]
Iteration: 109: X = [-11.637188    -0.79202247] | y = [146.51772]
Iteration: 110: X = [-8.142279   1.7031255] | y = [102.00674]
Iteration: 111: X = [-6.2424603 -2.2342901] | y = [162.02441]
Iteration: 112: X = [-9.567385   2.4119902] | y = 

Iteration: 79: X = [-13.964165   -1.4691241] | y = [184.94781]
Iteration: 80: X = [-9.625389   -0.61013913] | y = [123.964226]
Iteration: 81: X = [-13.232656    -0.79269266] | y = [159.5229]
Iteration: 82: X = [-11.682657    1.6611075] | y = [54.446854]
Iteration: 83: X = [-11.381424  -2.776519] | y = [201.80298]
Iteration: 84: X = [-6.456435  -2.0161195] | y = [156.0154]
Iteration: 85: X = [-13.618152   -2.0819569] | y = [198.44226]
Iteration: 86: X = [-10.451281     0.70079327] | y = [62.574425]
Iteration: 87: X = [-7.656999  2.333871] | y = [132.2193]
Iteration: 88: X = [-8.792353  1.159256] | y = [62.157173]
Iteration: 89: X = [-9.973673   1.1993256] | y = [45.23123]
Iteration: 90: X = [-13.980323   -2.6174855] | y = [213.8617]
Iteration: 91: X = [-12.774955    -0.23154163] | y = [136.53915]
Iteration: 92: X = [-10.809685     0.23178673] | y = [96.79167]
Iteration: 93: X = [-13.042952    2.0275002] | y = [57.154358]
Iteration: 94: X = [-6.9960155 -0.7447643] | y = [111.12489]
Itera

...

Iteration: 75: X = [-6.3591218   0.37100494] | y = [18.30642836]
Iteration: 76: X = [-5.84472299  0.3679651 ] | y = [16.27646402]
Iteration: 77: X = [-6.3242799   0.38881516] | y = [10.59611254]
Iteration: 78: X = [-5.85522532  0.32695055] | y = [12.64544947]
Iteration: 79: X = [-6.17840052  0.38927722] | y = [8.72780192]
Iteration: 80: X = [-5.23787737  0.26787543] | y = [8.0963232]
Iteration: 81: X = [-6.17212415  0.35204172] | y = [17.04105605]
Iteration: 82: X = [-5.75858772  0.339396  ] | y = [8.8643611]
Iteration: 83: X = [-5.94155133  0.34452045] | y = [9.26005961]
Iteration: 84: X = [-5.63576281  0.34352696] | y = [16.13983286]
Iteration: 85: X = [-5.69721937  0.28346515] | y = [20.32058651]
Iteration: 86: X = [-6.2626636   0.38418961] | y = [8.99278977]
Iteration: 87: X = [-5.91272175  0.36228383] | y = [11.30188543]
Iteration: 88: X = [-5.70578635  0.34658754] | y = [14.54382497]
Iteration: 89: X = [-5.30922472  0.31963742] | y = [19.47851757]
Iteration: 90: X = [-5.01275897 

Iteration: 52: X = [-1.67876261  0.49996591] | y = [0.46577198]
Iteration: 53: X = [-0.17080486 -1.06341058] | y = [0.8884006]
Iteration: 54: X = [-0.62169975  1.21271348] | y = [3.26645768]
Iteration: 55: X = [ 1.67832506 -0.81241262] | y = [-0.20620031]
Iteration: 56: X = [0.12797642 1.17091775] | y = [2.24970097]
Iteration: 57: X = [-1.66212273  1.0939219 ] | y = [1.17444126]
Iteration: 58: X = [-1.76889414 -0.61369383] | y = [2.31373348]
Iteration: 59: X = [ 1.73045075 -1.21750808] | y = [2.85083057]
Iteration: 60: X = [0.88889372 0.02343631] | y = [2.03254533]
Iteration: 61: X = [-0.81169903  0.81275201] | y = [0.26258134]
Iteration: 62: X = [-0.47996235  0.72193146] | y = [-0.53061609]
Iteration: 63: X = [ 1.22120762 -0.68994045] | y = [0.56012751]
Iteration: 64: X = [0.16726005 0.65471101] | y = [-0.75986029]
Iteration: 65: X = [-0.09126556  0.23858809] | y = [-0.20333839]
Iteration: 66: X = [1.68678617 0.17636013] | y = [2.23535697]
Iteration: 67: X = [ 1.30185914 -0.1698842 ] 

Iteration: 29: X = [1.16865706 0.29258561] | y = [2.423914]
Iteration: 30: X = [0.91936648 0.2304039 ] | y = [2.0926922]
Iteration: 31: X = [0.91822886 0.1071744 ] | y = [2.13249118]
Iteration: 32: X = [1.11347044 0.1102519 ] | y = [2.44125212]
Iteration: 33: X = [ 0.74549246 -0.33400857] | y = [0.9861681]
Iteration: 34: X = [1.0980556  0.31305265] | y = [2.3444199]
Iteration: 35: X = [ 0.96644568 -0.22361445] | y = [1.76953874]
Iteration: 36: X = [0.96937001 0.87021852] | y = [2.28933641]
Iteration: 37: X = [ 0.94761515 -0.09582305] | y = [2.01271441]
Iteration: 38: X = [1.32519794 0.10943365] | y = [2.4511192]
Iteration: 39: X = [0.97791374 0.05989051] | y = [2.2405303]
Iteration: 40: X = [1.14626491 0.45256591] | y = [2.25367652]
Iteration: 41: X = [0.88835621 0.16078615] | y = [2.05476018]
Iteration: 42: X = [ 0.98715556 -0.62510324] | y = [0.64285662]
Iteration: 43: X = [0.51270032 0.73959661] | y = [0.30042723]
Iteration: 44: X = [0.59712625 0.71819568] | y = [0.60421889]
Iterati

Iteration: 6: X = [1.20253193 0.38202786] | y = [2.36171904]
Iteration: 7: X = [1.63663352 0.87297463] | y = [2.75683695]
Iteration: 8: X = [1.13890743 0.50838137] | y = [2.19504378]
Iteration: 9: X = [1.36853635 0.80326796] | y = [2.49888912]
Iteration: 10: X = [1.31077087 0.43374109] | y = [2.32159069]
Iteration: 11: X = [1.4674108  0.55364871] | y = [2.1663572]
Iteration: 12: X = [1.40559268 0.82132268] | y = [2.55267168]
Iteration: 13: X = [1.32646358 0.20319581] | y = [2.46364079]
Iteration: 14: X = [1.4825685  0.48607588] | y = [2.18498533]
Iteration: 15: X = [1.22423422 0.66216731] | y = [2.22585543]
Iteration: 16: X = [1.60185885 0.53474736] | y = [2.10853215]
Iteration: 17: X = [1.57541835 0.62349916] | y = [2.11975324]
Iteration: 18: X = [1.64923847 0.71706772] | y = [2.23466363]
Iteration: 19: X = [ 1.91196728 -0.28954315] | y = [1.98221167]
Iteration: 20: X = [ 2.06628871 -0.30586052] | y = [3.76927424]
Iteration: 21: X = [ 1.71254611 -0.10171628] | y = [1.86193667]
Iterati

Iteration: 133: X = [ 0.12422097 -0.73280406] | y = [-1.02432851]
Iteration: 134: X = [ 0.06083    -0.69992578] | y = [-1.02739571]
Iteration: 135: X = [-1.76079592  0.47422218] | y = [0.61731171]
Iteration: 136: X = [-1.50029343  0.79785252] | y = [0.04287505]
Iteration: 137: X = [-0.05107087  0.72323394] | y = [-1.02438912]
Iteration: 138: X = [-1.9060708   1.20638394] | y = [3.1499856]
Iteration: 139: X = [-1.91484064  0.82653642] | y = [0.41683421]
Iteration: 140: X = [-0.1206944   0.71305823] | y = [-1.02795243]
Iteration: 141: X = [-0.16746515  0.73050523] | y = [-1.00727413]
Iteration: 142: X = [ 0.11153662 -0.68904209] | y = [-1.02487172]
Iteration: 143: X = [-0.09165949  0.70597911] | y = [-1.03124171]
Iteration: 144: X = [-0.02908212  0.70915675] | y = [-1.01720849]
Iteration: 145: X = [-0.13296926  0.71794939] | y = [-1.02444157]
Iteration: 146: X = [ 0.07637286 -0.69992375] | y = [-1.02978672]
Iteration: 147: X = [-1.47352588  1.53247881] | y = [12.60642969]
Iteration: 148:

In [ ]:
output_dir = "/Users/liao/Documents/BObystep/python_botorch/results/"
for dfn in dfn_list:
    for acq in acq_list:
        optim_benchmark(dfn, acq, output_dir)

Iteration 0
Iteration: 1: X = [0.] | y = [3.02721]
Iteration: 2: X = [0.] | y = [3.02721]
Iteration: 3: X = [0.09952391] | y = [-0.6486542]
Iteration: 4: X = [0.21773139] | y = [-0.47301355]
Iteration: 5: X = [0.21285607] | y = [-0.51845026]
Iteration: 6: X = [0.14100361] | y = [-0.98593926]
Iteration: 7: X = [0.4070731] | y = [0.15148012]
Iteration: 8: X = [0.5363191] | y = [0.96210116]
Iteration: 9: X = [0.14842935] | y = [-0.9812865]
Iteration: 10: X = [0.13906543] | y = [-0.98439986]
Iteration: 11: X = [0.14074484] | y = [-0.9858023]
Iteration: 12: X = [0.14133555] | y = [-0.9860845]
Iteration: 13: X = [0.140598] | y = [-0.98571527]
Iteration: 14: X = [0.14395088] | y = [-0.98604494]
Iteration: 15: X = [0.14085685] | y = [-0.98586416]
Iteration: 16: X = [0.14149694] | y = [-0.98614264]
Iteration: 17: X = [0.14473532] | y = [-0.98563147]
Iteration: 18: X = [0.1402695] | y = [-0.985496]
Iteration: 19: X = [0.14153366] | y = [-0.9861547]
Iteration: 20: X = [0.14493927] | y = [-0.98549

Iteration: 14: X = [0.14080349] | y = [-0.98583513]
Iteration: 15: X = [0.14258239] | y = [-0.9863254]
Iteration: 16: X = [0.1420539] | y = [-0.9862817]
Iteration: 17: X = [0.14188467] | y = [-0.9862495]
Iteration: 18: X = [0.14561369] | y = [-0.9849535]
Iteration: 19: X = [0.1380559] | y = [-0.9831226]
Iteration: 20: X = [0.14403257] | y = [-0.9860104]
Iteration: 21: X = [0.1447052] | y = [-0.9856507]
Iteration: 22: X = [0.14090562] | y = [-0.9858899]
Iteration: 23: X = [0.14183557] | y = [-0.98623854]
Iteration: 24: X = [0.14510977] | y = [-0.9853701]
Iteration: 25: X = [0.14265779] | y = [-0.9863247]
Iteration: 26: X = [0.14248285] | y = [-0.98632365]
Iteration: 27: X = [0.14144117] | y = [-0.98612344]
Iteration: 28: X = [0.14341122] | y = [-0.9862229]
Iteration: 29: X = [0.14032] | y = [-0.98553187]
Iteration: 30: X = [0.14165719] | y = [-0.9861925]
Iteration 6
Iteration: 1: X = [0.] | y = [3.02721]
Iteration: 2: X = [0.] | y = [3.02721]
Iteration: 3: X = [0.09950957] | y = [-0.648

Iteration: 27: X = [0.14024685] | y = [-0.9854796]
Iteration: 28: X = [0.14374009] | y = [-0.98612475]
Iteration: 29: X = [0.1393766] | y = [-0.9847274]
Iteration: 30: X = [0.14196958] | y = [-0.98626673]
Iteration 11
Iteration: 1: X = [0.] | y = [3.02721]
Iteration: 2: X = [0.] | y = [3.02721]
Iteration: 3: X = [0.09952331] | y = [-0.64864427]
Iteration: 4: X = [0.2177339] | y = [-0.47299045]
Iteration: 5: X = [0.21284452] | y = [-0.5185587]
Iteration: 6: X = [0.14090568] | y = [-0.9858899]
Iteration: 7: X = [0.4090651] | y = [0.16285484]
Iteration: 8: X = [0.538075] | y = [0.9544011]
Iteration: 9: X = [0.14811303] | y = [-0.98180985]
Iteration: 10: X = [0.13893615] | y = [-0.9842546]
Iteration: 11: X = [0.14113244] | y = [-0.9859997]
Iteration: 12: X = [0.14197724] | y = [-0.9862681]
Iteration: 13: X = [0.14166994] | y = [-0.9861961]
Iteration: 14: X = [0.1415059] | y = [-0.9861457]
Iteration: 15: X = [0.1380644] | y = [-0.98313475]
Iteration: 16: X = [0.14449915] | y = [-0.9857752]


Iteration: 10: X = [0.13903193] | y = [-0.9843627]
Iteration: 11: X = [0.1400828] | y = [-0.9853562]
Iteration: 12: X = [0.14091006] | y = [-0.98589224]
Iteration: 13: X = [0.14240791] | y = [-0.9863204]
Iteration: 14: X = [0.1426172] | y = [-0.9863253]
Iteration: 15: X = [0.14336284] | y = [-0.98623455]
Iteration: 16: X = [0.13996848] | y = [-0.9852651]
Iteration: 17: X = [0.14537007] | y = [-0.98516417]
Iteration: 18: X = [0.14109084] | y = [-0.9859808]
Iteration: 19: X = [0.14525762] | y = [-0.9852555]
Iteration: 20: X = [0.1413767] | y = [-0.9861001]
Iteration: 21: X = [0.14157109] | y = [-0.9861667]
Iteration: 22: X = [0.14349824] | y = [-0.98620015]
Iteration: 23: X = [0.14278463] | y = [-0.98631954]
Iteration: 24: X = [0.14084242] | y = [-0.9858564]
Iteration: 25: X = [0.14409004] | y = [-0.985985]
Iteration: 26: X = [0.14386103] | y = [-0.9860805]
Iteration: 27: X = [0.14230101] | y = [-0.9863127]
Iteration: 28: X = [0.14059299] | y = [-0.9857122]
Iteration: 29: X = [0.1391195]

Iteration: 23: X = [0.14465654] | y = [-0.9856813]
Iteration: 24: X = [0.14383723] | y = [-0.98608965]
Iteration: 25: X = [0.13968343] | y = [-0.98502004]
Iteration: 26: X = [0.14091831] | y = [-0.9858965]
Iteration: 27: X = [0.13992792] | y = [-0.9852319]
Iteration: 28: X = [0.14302927] | y = [-0.98629606]
Iteration: 29: X = [0.14167315] | y = [-0.986197]
Iteration: 30: X = [0.14156261] | y = [-0.98616403]
Iteration 22
Iteration: 1: X = [0.] | y = [3.02721]
Iteration: 2: X = [0.] | y = [3.02721]
Iteration: 3: X = [0.09951232] | y = [-0.64846027]
Iteration: 4: X = [0.21771935] | y = [-0.47312477]
Iteration: 5: X = [0.21285252] | y = [-0.51848364]
Iteration: 6: X = [0.14089327] | y = [-0.9858834]
Iteration: 7: X = [0.40723246] | y = [0.15237331]
Iteration: 8: X = [0.53572905] | y = [0.9644393]
Iteration: 9: X = [0.14733212] | y = [-0.98298234]
Iteration: 10: X = [0.13900347] | y = [-0.9843309]
Iteration: 11: X = [0.14035119] | y = [-0.9855536]
Iteration: 12: X = [0.14066322] | y = [-0.9

...

Iteration: 58: X = [-1.7032175  1.8423294] | y = [61.195892]
Iteration: 59: X = [ 3.194478 11.985119] | y = [95.49332]
Iteration: 60: X = [-0.15375805 14.904438  ] | y = [94.42677]
Iteration: 61: X = [ 9.5543  14.69263] | y = [147.03856]
Iteration: 62: X = [2.8116655 4.4128537] | y = [4.39957]
Iteration: 63: X = [0.8731599  0.41569808] | y = [34.59932]
Iteration: 64: X = [ 1.889988 13.692776] | y = [111.83075]
Iteration: 65: X = [-2.3324518 12.837037 ] | y = [9.239557]
Iteration: 66: X = [-0.3828373  6.8500085] | y = [18.956184]
Iteration: 67: X = [-3.1842892  8.8574095] | y = [12.800106]
Iteration: 68: X = [-4.525978  5.588962] | y = [113.501015]
Iteration: 69: X = [7.7342224 2.3830013] | y = [12.07806]
Iteration: 70: X = [7.718891  9.1694145] | y = [71.47098]
Iteration: 71: X = [ 8.32266  11.007529] | y = [92.25074]
Iteration: 72: X = [ 6.808178 14.008111] | y = [183.58038]
Iteration: 73: X = [3.6263103 7.2143717] | y = [29.456686]
Iteration: 74: X = [-3.8934493  5.6161094] | y = [75

Iteration: 37: X = [9.756692 3.239125] | y = [1.1427879]
Iteration: 38: X = [9.215894 2.303939] | y = [0.60660934]
Iteration: 39: X = [8.952316 1.052413] | y = [2.558375]
Iteration: 40: X = [9.445726 4.417151] | y = [4.103397]
Iteration: 41: X = [9.306614  3.0526235] | y = [0.92113686]
Iteration: 42: X = [9.015842   0.21190922] | y = [4.9522624]
Iteration: 43: X = [9.945809  1.9269462] | y = [2.7177896]
Iteration: 44: X = [9.444718  2.4424458] | y = [0.40223885]
Iteration: 45: X = [9.986739  4.2877426] | y = [3.5591736]
Iteration: 46: X = [9.3880415 3.8684013] | y = [2.4327521]
Iteration: 47: X = [9.365621  1.7345341] | y = [0.8921919]
Iteration: 48: X = [9.856332   0.95412934] | y = [4.92235]
Iteration: 49: X = [8.875774  0.8386439] | y = [3.2783914]
Iteration: 50: X = [9.977479  3.3568344] | y = [1.9690418]
Iteration: 51: X = [9.34617  3.962511] | y = [2.8394084]
Iteration: 52: X = [9.366734  0.7698507] | y = [3.1584578]
Iteration: 53: X = [0.8991928 7.838449 ] | y = [25.992739]
Iter

Iteration: 15: X = [7.266227  2.0472503] | y = [15.950183]
Iteration: 16: X = [ 4.721258 14.431179] | y = [180.79863]
Iteration: 17: X = [ 7.2939243 13.730544 ] | y = [170.51202]
Iteration: 18: X = [ 4.7452993 13.038962 ] | y = [146.79396]
Iteration: 19: X = [8.714364  4.1135807] | y = [7.4410415]
Iteration: 20: X = [ 6.843093 10.027305] | y = [96.794754]
Iteration: 21: X = [-3.139173   5.4748836] | y = [46.56046]
Iteration: 22: X = [-0.9425788 12.643703 ] | y = [40.93171]
Iteration: 23: X = [ 0.32145977 11.8975725 ] | y = [60.017036]
Iteration: 24: X = [-4.9688244  3.1383924] | y = [207.29474]
Iteration: 25: X = [1.1538053 7.919942 ] | y = [26.736177]
Iteration: 26: X = [9.531992  4.5181327] | y = [4.2602406]
Iteration: 27: X = [9.996624  1.2072105] | y = [5.1382437]
Iteration: 28: X = [9.928628  2.0868623] | y = [2.306756]
Iteration: 29: X = [9.871968   0.28624582] | y = [8.059555]
Iteration: 30: X = [9.86301   3.0200908] | y = [1.3279438]
Iteration: 31: X = [9.78035   2.1450796] | y

Iteration: 73: X = [7.335037 9.979127] | y = [90.499565]
Iteration: 74: X = [ 4.428093 13.302324] | y = [146.9436]
Iteration: 75: X = [8.175398  1.3314452] | y = [7.0514627]
Iteration: 76: X = [9.910213   0.08868344] | y = [9.494805]
Iteration: 77: X = [-4.372375 11.525952] | y = [22.028011]
Iteration: 78: X = [ 1.7580357 11.032843 ] | y = [63.440884]
Iteration: 79: X = [6.995145 4.191428] | y = [26.289309]
Iteration: 80: X = [ 8.921972 12.21077 ] | y = [104.1472]
Iteration 6
Iteration: 1: X = [3.8406668 1.0192164] | y = [3.2488446]
Iteration: 2: X = [7.512347  3.8860443] | y = [19.728355]
Iteration: 3: X = [ 8.487691 11.586199] | y = [100.123276]
Iteration: 4: X = [ 8.703078 13.831848] | y = [144.36212]
Iteration: 5: X = [-1.5575595 11.279412 ] | y = [16.312664]
Iteration: 6: X = [1.0480347 4.2802877] | y = [14.831577]
Iteration: 7: X = [4.9304037  0.07610963] | y = [13.558533]
Iteration: 8: X = [ 8.895252 11.689916] | y = [94.36046]
Iteration: 9: X = [ 4.236865 11.462425] | y = [103.

Iteration: 52: X = [-2.9683907  5.2159853] | y = [44.719433]
Iteration: 53: X = [9.332234  1.1174951] | y = [2.0787811]
Iteration: 54: X = [-2.1053755 13.250019 ] | y = [16.174099]
Iteration: 55: X = [ 8.039193 14.463136] | y = [174.87122]
Iteration: 56: X = [8.061345 1.954165] | y = [8.174512]
Iteration: 57: X = [ 7.8303967 13.654647 ] | y = [158.97246]
Iteration: 58: X = [9.527046 6.072126] | y = [12.764704]
Iteration: 59: X = [8.4852085 3.6959004] | y = [7.941182]
Iteration: 60: X = [8.619504 9.04967 ] | y = [54.75782]
Iteration: 61: X = [ 1.3203964 11.504888 ] | y = [66.86052]
Iteration: 62: X = [ 2.6199841 13.199879 ] | y = [111.56699]
Iteration: 63: X = [8.659016 7.549082] | y = [34.936005]
Iteration: 64: X = [ 2.457602 14.065486] | y = [127.92239]
Iteration: 65: X = [-4.9712257 12.792013 ] | y = [31.055256]
Iteration: 66: X = [ 6.052828 11.737903] | y = [132.52356]
Iteration: 67: X = [-4.874461 14.242794] | y = [18.229712]
Iteration: 68: X = [2.882244   0.17164436] | y = [6.0749

### for one example 

In [5]:
for _ in range(30):
    X = init_X
    Y = init_Y
    cov_abnormal = []
    for i in range(budget):
        large_jitter = False
        model = botorch.models.SingleTaskGP(X, Y)
        # train_Yvar = torch.full_like(Y, 0)# Force the noise level to 0
        # model = botorch.models.FixedNoiseGP(X, Y, train_Yvar)
        mll = ExactMarginalLogLikelihood(model.likelihood, model)
        try:# The package would automatically add jitter (diag) up to 1e-4, if fail, we mannually add jitter of 0.1
            fit_gpytorch_torch(mll, options={"maxiter": 3000, "lr": 0.01, "disp": False})
            # _ = fit_gpytorch_torch(mll)
        except:
            # print(f'{i}-th iteration added 0.1')
            try:
                with gpytorch.settings.cholesky_jitter(1e-1):
                    fit_gpytorch_torch(mll, options={"maxiter": 3000, "lr": 0.01, "disp": False})
                    # _ = fit_gpytorch_torch(mll)
                large_jitter = True
                cov_abnormal.append((i, model.covar_module(X).numpy()))
            except:
              # print(f'{i}-th iteration 0.1 would not enough!')
              break
        # print(f'{i}-th iteration ended')
    
        acquisition = botorch.acquisition.analytic.ExpectedImprovement(model, torch.max(Y), maximize=True)#EI as acquisation
    
        if large_jitter == False:
            candidates, acqui_value = optimize_acqf(acq_function=acquisition, 
                                                # bounds = torch.tensor([[0., 0.], [1., 1.]]),
                                                bounds=test_fun.bounds,
                                                q=1,
                                                num_restarts=20,
                                                raw_samples=512,
                                                sequential=False,
                                                )
        else:
            with gpytorch.settings.cholesky_jitter(1e-1):
                candidates, acqui_value = optimize_acqf(acq_function=acquisition,
                                                    # bounds = torch.tensor([[0., 0.], [1., 1.]]),
                                                    bounds=test_fun.bounds,
                                                    q=1,
                                                    num_restarts=20,
                                                    raw_samples=512,
                                                    sequential=False,
                                                   )
        newY = test_fun(candidates).view(-1, 1)
        X = torch.cat((X, candidates), dim=0)
        Y = torch.cat((Y, newY), dim=0)
        print(f"Iteration {i}: X = {candidates.numpy()} | y = { - newY.numpy()}")

/Users/liao/opt/anaconda3/envs/tf25/lib/python3.7/site-packages/gpytorch/lazy/triangular_lazy_tensor.py:130: UserWarning: torch.triangular_solve is deprecated in favor of torch.linalg.solve_triangularand will be removed in a future PyTorch release.
torch.linalg.solve_triangular has its arguments reversed and does not return a copy of one of the inputs.
X = torch.triangular_solve(B, A).solution
should be replaced with
X = torch.linalg.solve_triangular(A, B). (Triggered internally at  /Users/distiller/project/pytorch/aten/src/ATen/native/BatchLinearAlgebra.cpp:1672.)
  res = torch.triangular_solve(right_tensor, self.evaluate(), upper=self.upper).solution


Iteration 0: X = [[-0.12282776  1.2066659 ]] | y = [[2.567727]]
Iteration 1: X = [[-0.18474437  1.1147753 ]] | y = [[1.1346958]]
Iteration 2: X = [[-0.22973695  0.994516  ]] | y = [[-0.06643455]]
Iteration 3: X = [[-0.21553661  0.83430445]] | y = [[-0.8447335]]
Iteration 4: X = [[-0.18434529  0.7416644 ]] | y = [[-0.99317527]]
Iteration 5: X = [[-0.18385056  0.71554995]] | y = [[-0.9981594]]
Iteration 6: X = [[-0.24093106  0.73792946]] | y = [[-0.9446746]]
Iteration 7: X = [[-0.17430177  0.7109031 ]] | y = [[-1.0042003]]
Iteration 8: X = [[-0.24121203  0.7363684 ]] | y = [[-0.9447951]]
Iteration 9: X = [[-0.1721259   0.71311414]] | y = [[-1.0057796]]
Iteration 10: X = [[-0.23925287  0.73678315]] | y = [[-0.94678384]]
Iteration 11: X = [[-0.1705378  0.7171251]] | y = [[-1.0069181]]
Iteration 12: X = [[-0.23708834  0.7380317 ]] | y = [[-0.94872224]]
Iteration 13: X = [[-0.16929051  0.7212772 ]] | y = [[-1.0075465]]
Iteration 14: X = [[-0.16986838  0.72332525]] | y = [[-1.0070367]]
Iterat

Iteration 24: X = [[-0.18302864  0.707005  ]] | y = [[-0.99774826]]
Iteration 25: X = [[-0.18367878  0.70888776]] | y = [[-0.9976081]]
Iteration 26: X = [[-0.24069847  0.74951434]] | y = [[-0.94038486]]
Iteration 27: X = [[-0.1830819  0.7113386]] | y = [[-0.99836004]]
Iteration 28: X = [[-0.2394736   0.75055736]] | y = [[-0.9411458]]
Iteration 29: X = [[-0.18223509  0.71320343]] | y = [[-0.9991361]]
Iteration 30: X = [[-0.23820673  0.75141066]] | y = [[-0.9420199]]
Iteration 31: X = [[-0.18148342  0.715059  ]] | y = [[-0.999781]]
Iteration 32: X = [[-0.18217961  0.7166575 ]] | y = [[-0.99936414]]
Iteration 33: X = [[-0.23710765  0.753713  ]] | y = [[-0.9418678]]
Iteration 34: X = [[-0.18148543  0.71890455]] | y = [[-0.999857]]
Iteration 35: X = [[-0.23584673  0.75479096]] | y = [[-0.94252264]]
Iteration 36: X = [[-0.18113127  0.7202612 ]] | y = [[-1.0000662]]
Iteration 37: X = [[-0.18184672  0.7224136 ]] | y = [[-0.99946475]]
Iteration 38: X = [[-0.23490082  0.756982  ]] | y = [[-0.942

Iteration 47: X = [[ 0.01164151 -0.82368344]] | y = [[-0.88166296]]
Iteration 48: X = [[ 0.07073907 -0.81591046]] | y = [[-0.9279142]]
Iteration 49: X = [[ 0.01218267 -0.82451653]] | y = [[-0.8800995]]
Iteration 0: X = [[ 0.26531273 -2.        ]] | y = [[47.74065]]
Iteration 1: X = [[ 2.9916453 -1.9604881]] | y = [[144.40576]]
Iteration 2: X = [[-1.8241792  0.5468364]] | y = [[0.50341153]]
Iteration 3: X = [[-1.6748217  0.6824284]] | y = [[-0.08448684]]
Iteration 4: X = [[-1.6690704  1.0088389]] | y = [[0.44079933]]
Iteration 5: X = [[-1.6698688  -0.20254183]] | y = [[2.2333612]]
Iteration 6: X = [[-1.691516  2.      ]] | y = [[46.677902]]
Iteration 7: X = [[-1.3872952 -1.9427488]] | y = [[46.87474]]
Iteration 8: X = [[-1.9010406 -2.       ]] | y = [[54.56405]]
Iteration 9: X = [[-0.80435205  1.941519  ]] | y = [[41.99593]]
Iteration 10: X = [[1.1178207 1.8826916]] | y = [[40.550755]]
Iteration 11: X = [[-1.3244672  1.8847907]] | y = [[36.127106]]
Iteration 12: X = [[-0.10934091  1.965

Iteration 24: X = [[-0.95143586  1.2845082 ]] | y = [[5.2148714]]
Iteration 25: X = [[-0.94840384 -2.        ]] | y = [[52.03826]]
Iteration 26: X = [[ 1.4337227  -0.31973946]] | y = [[1.4186467]]
Iteration 27: X = [[ 1.439723  -0.3181899]] | y = [[1.4150622]]
Iteration 28: X = [[ 1.4441222 -0.3170568]] | y = [[1.412402]]
Iteration 29: X = [[ 1.4474846  -0.31624204]] | y = [[1.4101796]]
Iteration 30: X = [[ 1.4502125  -0.31554893]] | y = [[1.408483]]
Iteration 31: X = [[ 1.4525344  -0.31511036]] | y = [[1.40651]]
Iteration 32: X = [[ 1.45449    -0.31457934]] | y = [[1.4054091]]
Iteration 33: X = [[ 1.4562924  -0.31420913]] | y = [[1.4039787]]
Iteration 34: X = [[ 1.457859   -0.31394157]] | y = [[1.4025476]]
Iteration 35: X = [[ 1.4593201  -0.31366527]] | y = [[1.4013047]]
Iteration 36: X = [[ 1.4606808 -0.3134506]] | y = [[1.3999977]]
Iteration 37: X = [[ 1.4620979 -0.313282 ]] | y = [[1.3984482]]
Iteration 38: X = [[ 1.4633061  -0.31324458]] | y = [[1.3967559]]
Iteration 39: X = [[ 1.

...

Iteration 29: X = [[-0.04175691  0.70525634]] | y = [[-1.0224539]]
Iteration 30: X = [[-0.01089998  0.7561721 ]] | y = [[-0.9871482]]
Iteration 31: X = [[-0.03773536  0.70505816]] | y = [[-1.0208805]]
Iteration 32: X = [[-0.00800613  0.75527215]] | y = [[-0.98594546]]
Iteration 33: X = [[-0.03370034  0.7048743 ]] | y = [[-1.0191746]]
Iteration 34: X = [[-0.00418009  0.75473696]] | y = [[-0.98369277]]
Iteration 35: X = [[-0.03025849  0.7049053 ]] | y = [[-1.0176302]]
Iteration 36: X = [[-0.02851025  0.7060503 ]] | y = [[-1.0168707]]
Iteration 37: X = [[3.3414512e-04 7.5434238e-01]] | y = [[-0.9806856]]
Iteration 38: X = [[-0.02453316  0.7059353 ]] | y = [[-1.0149012]]
Iteration 39: X = [[0.00398963 0.7539381 ]] | y = [[-0.97820175]]
Iteration 40: X = [[-0.02026451  0.70591176]] | y = [[-1.0126513]]
Iteration 41: X = [[0.00649095 0.7535062 ]] | y = [[-0.9765686]]
Iteration 42: X = [[-0.01792019  0.70576745]] | y = [[-1.011349]]
Iteration 43: X = [[0.00884414 0.7529111 ]] | y = [[-0.97513

Iteration 4: X = [[0.46172342 0.19776668]] | y = [[0.701526]]
Iteration 5: X = [[0.45372015 0.06752587]] | y = [[0.7498418]]
Iteration 6: X = [[ 0.4513436 -0.6235625]] | y = [[-0.50149024]]
Iteration 7: X = [[ 0.45605373 -2.        ]] | y = [[47.83199]]
Iteration 8: X = [[0.6123105 1.8596206]] | y = [[36.36426]]
Iteration 9: X = [[-0.67615366  1.9269753 ]] | y = [[40.418205]]
Iteration 10: X = [[ 1.0353751 -1.9371113]] | y = [[41.59214]]
Iteration 11: X = [[0.02681541 1.8187728 ]] | y = [[30.589632]]
Iteration 12: X = [[-0.46041536 -1.9674764 ]] | y = [[46.11617]]
Iteration 13: X = [[ 0.5567744  -0.34009075]] | y = [[0.4496238]]
Iteration 14: X = [[ 0.5523117  -0.32964462]] | y = [[0.4647447]]
Iteration 15: X = [[ 0.46673024 -0.23263499]] | y = [[0.46180433]]
Iteration 16: X = [[ 0.6384421  -0.41993368]] | y = [[0.45501232]]
Iteration 17: X = [[ 0.683495   -0.22705637]] | y = [[1.0935569]]
Iteration 18: X = [[ 0.5976597  -0.44359413]] | y = [[0.2787029]]
Iteration 19: X = [[ 0.16252619

Iteration 30: X = [[-0.28394282  0.6233616 ]] | y = [[-0.81832266]]
Iteration 31: X = [[-0.22426231  0.61031306]] | y = [[-0.87592196]]
Iteration 32: X = [[-0.2826151  0.6249631]] | y = [[-0.8224739]]
Iteration 33: X = [[-0.22332181  0.60846466]] | y = [[-0.8742131]]
Iteration 34: X = [[-0.25463432  0.51631147]] | y = [[-0.6629095]]
Iteration 35: X = [[-0.2799435   0.62976956]] | y = [[-0.8328052]]
Iteration 36: X = [[-0.22469822  0.61752623]] | y = [[-0.8857882]]
Iteration 37: X = [[-0.22679278  0.620506  ]] | y = [[-0.88762224]]
Iteration 38: X = [[-0.28298435  0.6267035 ]] | y = [[-0.82431847]]
Iteration 39: X = [[-0.22353207  0.6142548 ]] | y = [[-0.8824283]]
Iteration 40: X = [[-0.25278875  0.52208275]] | y = [[-0.67795956]]
Iteration 41: X = [[-0.28108275  0.63025236]] | y = [[-0.83181065]]
Iteration 42: X = [[-0.22585766  0.6226976 ]] | y = [[-0.89161646]]
Iteration 43: X = [[-0.28087297  0.6301163 ]] | y = [[-0.83193225]]
Iteration 44: X = [[-0.22325683  0.6173902 ]] | y = [[-0

Iteration 5: X = [[-1.2615763  -0.42825675]] | y = [[2.331857]]
Iteration 6: X = [[-1.172852   1.5696347]] | y = [[14.980645]]
Iteration 7: X = [[-1.4707607 -1.8775177]] | y = [[40.56584]]
Iteration 8: X = [[-0.7826123  1.5831194]] | y = [[15.600196]]
Iteration 9: X = [[ 1.1271081 -1.9063483]] | y = [[38.519085]]
Iteration 10: X = [[-0.75641465 -1.7638112 ]] | y = [[29.267696]]
Iteration 11: X = [[0.6346886 1.989044 ]] | y = [[49.33868]]
Iteration 12: X = [[-1.1436965  1.9413536]] | y = [[41.90643]]
Iteration 13: X = [[-0.43779397  1.6798995 ]] | y = [[20.5243]]
Iteration 14: X = [[1.3659434 1.9911613]] | y = [[52.054794]]
Iteration 15: X = [[-0.24791574  1.8347886 ]] | y = [[31.649242]]
Iteration 16: X = [[-1.7569873 -1.0597036]] | y = [[4.5560956]]
Iteration 17: X = [[-1.7220426  1.899795 ]] | y = [[36.484734]]
Iteration 18: X = [[-1.1114078 -1.937391 ]] | y = [[45.858852]]
Iteration 19: X = [[-0.8419318   0.04850912]] | y = [[1.8487086]]
Iteration 20: X = [[ 0.17538404 -1.3534998 ]]

Iteration 31: X = [[0.6247127 0.7203396]] | y = [[0.712464]]
Iteration 32: X = [[0.6334517  0.72094655]] | y = [[0.7467054]]
Iteration 33: X = [[0.97081286 0.5559885 ]] | y = [[1.8691089]]
Iteration 34: X = [[0.60128134 0.73286635]] | y = [[0.63357943]]
Iteration 35: X = [[0.48619148 0.5754466 ]] | y = [[0.22642428]]
Iteration 36: X = [[0.4946753  0.57310885]] | y = [[0.25916648]]
Iteration 37: X = [[0.6034709  0.72835577]] | y = [[0.637559]]
Iteration 38: X = [[0.5452155  0.52892333]] | y = [[0.49463207]]
Iteration 39: X = [[0.59143835 0.7210984 ]] | y = [[0.58459187]]
Iteration 40: X = [[0.70162386 0.50207835]] | y = [[1.0980868]]
Iteration 41: X = [[0.934235  0.6317884]] | y = [[1.7440003]]
Iteration 42: X = [[0.41896683 0.63544047]] | y = [[-0.05751115]]
Iteration 43: X = [[0.42360526 0.6398992 ]] | y = [[-0.04408008]]
Iteration 44: X = [[0.5168011 0.7184866]] | y = [[0.29725122]]
Iteration 45: X = [[0.4300961  0.56450045]] | y = [[0.04450661]]
Iteration 46: X = [[0.43396702 0.5651